In [219]:
import argparse
import sys
import os
import json
import pprint
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import re
import torch
import math
from collections import Counter
from transformers import AutoModel, AutoTokenizer, pipeline
from tqdm import tqdm
from sklearn.metrics import f1_score

In [220]:
BASE_DIR = "/Users/katemarg/PycharmProjects/temporal_robustness_evaluation"
DATA_DIR = os.path.join(BASE_DIR, 'data')
CKPT_DIR = os.path.join(BASE_DIR, 'pretrained_models')
RES_DIR = os.path.join(BASE_DIR, 'results')
LOG_DIR = os.path.join(BASE_DIR, 'logs')
CACHE_DIR = os.path.join(BASE_DIR, 'cached')

TEMPLAMA_ORIG_DIR = os.path.join("data", "templama", "test.json")
TEMPLAMA_REPRODUCED_DIR = os.path.join("templama_docker", "reproduce1", "templama", "test.jsonl")
TEMPLAMA_NEW_DIR = os.path.join(DATA_DIR, "dynamic-templama",
                                "dataset_from_2019-1-1_to_2022-6-31_per_quarter", 
                                "test.jsonl")
lm = "cardiffnlp/twitter-roberta-base-mar2022"
# dataset_filepath=CACHE_DIR+'/{}_dynamic-templama_multiple_masks.pt'.format(lm)
dataset_filepath=CACHE_DIR+'/timelms_dynamic-templama_2019-1-1_to_2022-6-31_per_quarter_multi_token_splits.pt'

## Load dataset

In [221]:
data_dict_multi_token = torch.load(dataset_filepath)
data_dict_multi_token = data_dict_multi_token[0]
year='2019-Q2'
data_dict = data_dict_multi_token

In [222]:
data_dict_multi_token['2019-Q2']['text'][0]

'Alex Morgan plays for <mask>.'

In [223]:
data_dict_multi_token['2019-Q2']['labels'][0]

[' Orlando Pride']

In [224]:
data_dict_multi_token['2019-Q2']['labels_ids'][0]

[5854, 13170]

In [225]:
data = list(zip(data_dict[year]["text"], data_dict[year]["labels"], data_dict[year]["labels_ids"],
                data_dict[year]["relation"]))

In [226]:
sorted(
                        data, key=lambda k: len(k[2])
                )[:32]

[('Lewis Hamilton plays for <mask>.', [' Mercedes'], [7016], 'P54'),
 ('David Andersen plays for <mask>.', [' Hawks'], [10506], 'P54'),
 ('David Andersen plays for <mask>.', [' Hawks'], [10506], 'P54'),
 ('Sonny Bill Williams plays for <mask>.', [' Chiefs'], [6535], 'P54'),
 ('André Lotterer plays for <mask>.', [' Porsche'], [15091], 'P54'),
 ('Carlos Sainz Jr plays for <mask>.', [' McLaren'], [15081], 'P54'),
 ('Elinor Barker plays for <mask>.', [' Drops'], [43534], 'P54'),
 ('Matthew Goss plays for <mask>.', [' ONE'], [19551], 'P54'),
 ('Francis holds the position of <mask>.', [' pope'], [16627], 'P39'),
 ('Francis Collins holds the position of <mask>.',
  [' director'],
  [736],
  'P39'),
 ('John L. Hennessy holds the position of <mask>.',
  [' director'],
  [736],
  'P39'),
 ('Axel Kahn holds the position of <mask>.', [' president'], [394], 'P39'),
 ('Axel Kahn holds the position of <mask>.', [' president'], [394], 'P39'),
 ('Annegret Kramp-Karrenbauer holds the position of <mask>.

In [227]:
tokenizer.mask_token_id

50264

In [228]:
tokenizer = AutoTokenizer.from_pretrained(lm, use_fast=False, add_prefix_space=True)
fill_mask_model = pipeline(
    'fill-mask', model=lm, framework="pt", batch_size=32,
    tokenizer=tokenizer, top_k=len(tokenizer)
)
model = fill_mask_model.model
model.eval()
cuda = torch.cuda.is_available()
if cuda:
    model = model.cuda()
        
def tokenizer_return_id(tokenizer, text, filter_special_tokens=False):
    """
    Text to token ids for a string.
    """
    output = tokenizer(text)
    if filter_special_tokens:
        token_ids = [i for i in output['input_ids'] if i not in tokenizer.all_special_ids]
    else:
        token_ids = [i for i in output['input_ids'] ]
    return token_ids

pppl_list = []
# i=0
# # load data
# text_i = data_dict_multi_token['2019-Q2']['text'][i]  # contains only one <mask> independently of how many tokens the label has
# labels_i = data_dict_multi_token['2019-Q2']['labels'][i]
# labels_i_without_space = [label[1:] for label in labels_i if label[0]==' ']
# label_ids_i = data_dict_multi_token['2019-Q2']['labels_ids'][i]

# # add extra masks if needed
# num_correct_masks = len(label_ids_i)
# new_masks = " ".join(["<mask>"]*num_correct_masks)
# text_i = text_i.replace("<mask>", new_masks)
    
# # tokenize orig sentence (with masks)
# tokenized_sentence_with_masks = tokenizer_return_id(tokenizer, text_i)

# # where are the masks (indices)
# mask_inds = list(np.where(np.array(tokenized_sentence_with_masks) == tokenizer.mask_token_id)[0])

# # replace with correct labels
# tokenized_sentence_orig = [orig if i not in mask_inds else label_ids_i[mask_inds.index(i)] 
#                            for i,orig in enumerate(tokenized_sentence_with_masks) 
#                             ]

In [229]:
for i in range(len(data_dict_multi_token['2019-Q2']['text'])):
    print(i)
    # load data
    text_i = data_dict_multi_token['2019-Q2']['text'][i]  # contains only one <mask> independently of how many tokens the label has
    labels_i = data_dict_multi_token['2019-Q2']['labels'][i]
    labels_i_without_space = [label[1:] for label in labels_i if label[0]==' ']
    label_ids_i = data_dict_multi_token['2019-Q2']['labels_ids'][i]

    # add extra masks if needed
    num_correct_masks = len(label_ids_i)
    new_masks = " ".join(["<mask>"]*num_correct_masks)
    text_i = text_i.replace("<mask>", new_masks)

    # tokenize orig sentence (with masks)
    tokenized_sentence_with_masks = tokenizer_return_id(tokenizer, text_i)

    # where are the masks (indices)
    mask_inds = list(np.where(np.array(tokenized_sentence_with_masks) == tokenizer.mask_token_id)[0])

    # replace with correct labels
    tokenized_sentence_orig = [orig if i not in mask_inds else label_ids_i[mask_inds.index(i)] 
                               for i,orig in enumerate(tokenized_sentence_with_masks) 
                                ]
    sum_ppl = 0
    n_subtokens_total = num_correct_masks
    for mask_j in range(num_correct_masks):
#         print(mask_j)
        # find index of current mask (in tokenized seuence)
        index_of_current_mask = mask_inds[mask_j]

        # change it with mask id   
        tokenized_sentence = tokenized_sentence_orig.copy()
        tokenized_sentence[index_of_current_mask] = tokenizer.mask_token_id 
        print(tokenized_sentence)

        # correct label token id 
        current_correct_token_id = label_ids_i[mask_j]

        with torch.no_grad():
            # tensor
            inp = torch.tensor([tokenized_sentence]).cuda() if cuda else torch.tensor([tokenized_sentence])

            # get logits
            out = model(inp)
            logits = out.logits.detach().cpu()  # batch_size x max_len x vocab

            # logit for the correct token
            logits_for_mask = logits[:,index_of_current_mask][0]
            log_softmax_for_mask = logits_for_mask.log_softmax(-1)

            # log_softmax of correct label
            score = log_softmax_for_mask[current_correct_token_id].item()
#             print(score)
            sum_ppl += score
    pseudo_ppl = math.e**(-1*(sum_ppl/n_subtokens_total))
    print('PPPL: {}'.format(pseudo_ppl))
    pppl_list.append(pseudo_ppl)

0
[0, 2618, 3040, 1974, 13, 50264, 13170, 4, 2]
[0, 2618, 3040, 1974, 13, 5854, 50264, 4, 2]
PPPL: 206.07248932667864
1
[0, 15350, 9711, 1974, 13, 50264, 4612, 4, 2]
[0, 15350, 9711, 1974, 13, 5429, 50264, 4, 2]
PPPL: 1.0407436289298688
2
[0, 8767, 5472, 7991, 1974, 13, 50264, 274, 4, 347, 4, 4, 2]
[0, 8767, 5472, 7991, 1974, 13, 9573, 50264, 4, 347, 4, 4, 2]
[0, 8767, 5472, 7991, 1974, 13, 9573, 274, 50264, 347, 4, 4, 2]
[0, 8767, 5472, 7991, 1974, 13, 9573, 274, 4, 50264, 4, 4, 2]
[0, 8767, 5472, 7991, 1974, 13, 9573, 274, 4, 347, 50264, 4, 2]
PPPL: 4.442563887793119
3
[0, 9517, 957, 1974, 13, 50264, 1422, 6772, 4, 2]
[0, 9517, 957, 1974, 13, 1287, 50264, 6772, 4, 2]
[0, 9517, 957, 1974, 13, 1287, 1422, 50264, 4, 2]
PPPL: 1.1363056980195065
4
[0, 221, 5858, 5648, 225, 1974, 13, 50264, 15089, 4231, 36508, 17560, 4, 2]
[0, 221, 5858, 5648, 225, 1974, 13, 226, 50264, 4231, 36508, 17560, 4, 2]
[0, 221, 5858, 5648, 225, 1974, 13, 226, 15089, 50264, 36508, 17560, 4, 2]
[0, 221, 5858, 5648,

[0, 1653, 3572, 11732, 1974, 13, 10585, 73, 50264, 35733, 5429, 4, 2]
[0, 1653, 3572, 11732, 1974, 13, 10585, 73, 9873, 50264, 5429, 4, 2]
[0, 1653, 3572, 11732, 1974, 13, 10585, 73, 9873, 35733, 50264, 4, 2]
PPPL: 127.02709748534633
34
[0, 5465, 102, 1974, 13, 50264, 4168, 3314, 11489, 2586, 4, 2]
[0, 5465, 102, 1974, 13, 5429, 50264, 3314, 11489, 2586, 4, 2]
[0, 5465, 102, 1974, 13, 5429, 4168, 50264, 11489, 2586, 4, 2]
[0, 5465, 102, 1974, 13, 5429, 4168, 3314, 50264, 2586, 4, 2]
[0, 5465, 102, 1974, 13, 5429, 4168, 3314, 11489, 50264, 4, 2]
PPPL: 64.46657051800166
35
[0, 5465, 102, 1974, 13, 50264, 13170, 4, 2]
[0, 5465, 102, 1974, 13, 5854, 50264, 4, 2]
PPPL: 235.12363891504532
36
[0, 854, 4987, 705, 16496, 732, 895, 337, 1974, 13, 50264, 32109, 20434, 20071, 4, 2]
[0, 854, 4987, 705, 16496, 732, 895, 337, 1974, 13, 2930, 50264, 20434, 20071, 4, 2]
[0, 854, 4987, 705, 16496, 732, 895, 337, 1974, 13, 2930, 32109, 50264, 20071, 4, 2]
[0, 854, 4987, 705, 16496, 732, 895, 337, 1974, 1

[0, 871, 726, 6412, 1974, 13, 5429, 50264, 10489, 4, 2]
[0, 871, 726, 6412, 1974, 13, 5429, 10402, 50264, 4, 2]
PPPL: 1.4986854758624173
66
[0, 1577, 1843, 14856, 10319, 1343, 6841, 1974, 13, 50264, 632, 1037, 165, 4, 2]
[0, 1577, 1843, 14856, 10319, 1343, 6841, 1974, 13, 5092, 50264, 1037, 165, 4, 2]
[0, 1577, 1843, 14856, 10319, 1343, 6841, 1974, 13, 5092, 632, 50264, 165, 4, 2]
[0, 1577, 1843, 14856, 10319, 1343, 6841, 1974, 13, 5092, 632, 1037, 50264, 4, 2]
PPPL: 7.2889212694905945
67
[0, 1577, 1843, 14856, 10319, 1343, 6841, 1974, 13, 50264, 274, 4, 347, 4, 4, 2]
[0, 1577, 1843, 14856, 10319, 1343, 6841, 1974, 13, 3426, 50264, 4, 347, 4, 4, 2]
[0, 1577, 1843, 14856, 10319, 1343, 6841, 1974, 13, 3426, 274, 50264, 347, 4, 4, 2]
[0, 1577, 1843, 14856, 10319, 1343, 6841, 1974, 13, 3426, 274, 4, 50264, 4, 4, 2]
[0, 1577, 1843, 14856, 10319, 1343, 6841, 1974, 13, 3426, 274, 4, 347, 50264, 4, 2]
PPPL: 2.6152095785874754
68
[0, 5908, 5664, 1168, 1974, 13, 50264, 13114, 4, 2]
[0, 5908, 566

[0, 4833, 29667, 29, 256, 108, 387, 1168, 3592, 1974, 13, 21774, 632, 1037, 50264, 4, 2]
PPPL: 3.2375563105265797
95
[0, 4833, 29667, 29, 256, 108, 387, 1168, 3592, 1974, 13, 50264, 5967, 15247, 1343, 5429, 4, 2]
[0, 4833, 29667, 29, 256, 108, 387, 1168, 3592, 1974, 13, 381, 50264, 15247, 1343, 5429, 4, 2]
[0, 4833, 29667, 29, 256, 108, 387, 1168, 3592, 1974, 13, 381, 5967, 50264, 1343, 5429, 4, 2]
[0, 4833, 29667, 29, 256, 108, 387, 1168, 3592, 1974, 13, 381, 5967, 15247, 50264, 5429, 4, 2]
[0, 4833, 29667, 29, 256, 108, 387, 1168, 3592, 1974, 13, 381, 5967, 15247, 1343, 50264, 4, 2]
PPPL: 41.57732452896545
96
[0, 8966, 5925, 1974, 13, 50264, 17458, 632, 1037, 165, 4, 2]
[0, 8966, 5925, 1974, 13, 7505, 50264, 632, 1037, 165, 4, 2]
[0, 8966, 5925, 1974, 13, 7505, 17458, 50264, 1037, 165, 4, 2]
[0, 8966, 5925, 1974, 13, 7505, 17458, 632, 50264, 165, 4, 2]
[0, 8966, 5925, 1974, 13, 7505, 17458, 632, 1037, 50264, 4, 2]
PPPL: 1.8270876595832268
97
[0, 8966, 5925, 1974, 13, 50264, 1063, 272

[0, 20831, 11669, 119, 2507, 1974, 13, 1600, 632, 5259, 1037, 50264, 4, 2]
PPPL: 8.525447517228983
125
[0, 20831, 11669, 119, 2507, 1974, 13, 50264, 10402, 10489, 4, 2]
[0, 20831, 11669, 119, 2507, 1974, 13, 5429, 50264, 10489, 4, 2]
[0, 20831, 11669, 119, 2507, 1974, 13, 5429, 10402, 50264, 4, 2]
PPPL: 1.675478156117627
126
[0, 3292, 991, 14640, 15597, 4122, 118, 1974, 13, 50264, 37960, 163, 7110, 4, 2]
[0, 3292, 991, 14640, 15597, 4122, 118, 1974, 13, 5429, 50264, 163, 7110, 4, 2]
[0, 3292, 991, 14640, 15597, 4122, 118, 1974, 13, 5429, 37960, 50264, 7110, 4, 2]
[0, 3292, 991, 14640, 15597, 4122, 118, 1974, 13, 5429, 37960, 163, 50264, 4, 2]
PPPL: 191.44095361440185
127
[0, 7687, 3538, 1935, 5811, 6149, 225, 1974, 13, 50264, 12130, 1178, 4, 2]
[0, 7687, 3538, 1935, 5811, 6149, 225, 1974, 13, 12723, 50264, 1178, 4, 2]
[0, 7687, 3538, 1935, 5811, 6149, 225, 1974, 13, 12723, 12130, 50264, 4, 2]
PPPL: 4764.119136021975
128
[0, 13710, 179, 1999, 1974, 13, 50264, 3336, 1037, 165, 4, 2]
[0, 

...

PPPL: 132.07808327513155
10706
[0, 9767, 17057, 1243, 16, 2622, 30, 50264, 1792, 12839, 8484, 4, 2]
[0, 9767, 17057, 1243, 16, 2622, 30, 14228, 50264, 12839, 8484, 4, 2]
[0, 9767, 17057, 1243, 16, 2622, 30, 14228, 1792, 50264, 8484, 4, 2]
[0, 9767, 17057, 1243, 16, 2622, 30, 14228, 1792, 12839, 50264, 4, 2]
PPPL: 1.4810035858558643
10707
[0, 23633, 12482, 12, 1096, 16, 2622, 30, 50264, 4, 2]
PPPL: 14.207990827095676
10708
[0, 6482, 16, 2622, 30, 50264, 337, 415, 4, 2]
[0, 6482, 16, 2622, 30, 30471, 50264, 415, 4, 2]
[0, 6482, 16, 2622, 30, 30471, 337, 50264, 4, 2]
PPPL: 92.27438685215463
10709
[0, 6482, 16, 2622, 30, 50264, 7257, 21133, 4, 2]
[0, 6482, 16, 2622, 30, 226, 50264, 21133, 4, 2]
[0, 6482, 16, 2622, 30, 226, 7257, 50264, 4, 2]
PPPL: 61.79117906826155
10710
[0, 7346, 347, 17257, 3631, 12, 5944, 1105, 5471, 112, 35, 134, 4, 398, 6019, 5266, 16, 2622, 30, 50264, 2678, 4, 2]
[0, 7346, 347, 17257, 3631, 12, 5944, 1105, 5471, 112, 35, 134, 4, 398, 6019, 5266, 16, 2622, 30, 9039, 5

[0, 208, 18857, 1021, 571, 274, 267, 3109, 1728, 1384, 837, 16, 10, 1030, 1385, 11, 468, 50264, 15453, 14562, 219, 4, 2]
[0, 208, 18857, 1021, 571, 274, 267, 3109, 1728, 1384, 837, 16, 10, 1030, 1385, 11, 468, 11489, 50264, 14562, 219, 4, 2]
[0, 208, 18857, 1021, 571, 274, 267, 3109, 1728, 1384, 837, 16, 10, 1030, 1385, 11, 468, 11489, 15453, 50264, 219, 4, 2]
[0, 208, 18857, 1021, 571, 274, 267, 3109, 1728, 1384, 837, 16, 10, 1030, 1385, 11, 468, 11489, 15453, 14562, 50264, 4, 2]
PPPL: 89.33489370241661
10737
[0, 208, 18857, 1021, 571, 274, 267, 3109, 1728, 1384, 837, 16, 10, 1030, 1385, 11, 50264, 4, 2]
PPPL: 202689115.86215317
10738
[0, 208, 18857, 1021, 571, 274, 267, 3109, 1728, 1384, 837, 16, 10, 1030, 1385, 11, 50264, 45259, 4, 2]
[0, 208, 18857, 1021, 571, 274, 267, 3109, 1728, 1384, 837, 16, 10, 1030, 1385, 11, 10091, 50264, 4, 2]
PPPL: 1100.807411578048
10739
[0, 8051, 2071, 463, 1384, 837, 16, 10, 1030, 1385, 11, 50264, 14562, 571, 858, 4, 2]
[0, 8051, 2071, 463, 1384, 837, 

[0, 8603, 20375, 1384, 837, 16, 10, 1030, 1385, 11, 234, 50264, 338, 14562, 219, 4, 2]
[0, 8603, 20375, 1384, 837, 16, 10, 1030, 1385, 11, 234, 30422, 50264, 14562, 219, 4, 2]
[0, 8603, 20375, 1384, 837, 16, 10, 1030, 1385, 11, 234, 30422, 338, 50264, 219, 4, 2]
[0, 8603, 20375, 1384, 837, 16, 10, 1030, 1385, 11, 234, 30422, 338, 14562, 50264, 4, 2]
PPPL: 16.86398867391916
10770
[0, 8603, 20375, 1384, 837, 16, 10, 1030, 1385, 11, 50264, 2133, 4, 2]
[0, 8603, 20375, 1384, 837, 16, 10, 1030, 1385, 11, 16706, 50264, 4, 2]
PPPL: 1108.967512356846
10771
[0, 2083, 28235, 14562, 241, 1384, 837, 16, 10, 1030, 1385, 11, 50264, 4, 2]
PPPL: 367584435.90372103
10772
[0, 2083, 28235, 14562, 241, 1384, 837, 16, 10, 1030, 1385, 11, 50264, 20375, 4, 2]
[0, 2083, 28235, 14562, 241, 1384, 837, 16, 10, 1030, 1385, 11, 10910, 50264, 4, 2]
PPPL: 2938.4420466495544
10773
[0, 2083, 28235, 14562, 241, 1384, 837, 16, 10, 1030, 1385, 11, 50264, 1630, 2359, 4, 2]
[0, 2083, 28235, 14562, 241, 1384, 837, 16, 10, 1

[0, 312, 1469, 8395, 1384, 837, 16, 10, 1030, 1385, 11, 248, 24800, 14562, 50264, 4, 2]
PPPL: 1445.291317515088
10802
[0, 312, 1469, 8395, 1384, 837, 16, 10, 1030, 1385, 11, 50264, 14562, 219, 4, 2]
[0, 312, 1469, 8395, 1384, 837, 16, 10, 1030, 1385, 11, 14533, 50264, 219, 4, 2]
[0, 312, 1469, 8395, 1384, 837, 16, 10, 1030, 1385, 11, 14533, 14562, 50264, 4, 2]
PPPL: 4692.150020842972
10803
[0, 381, 7823, 28191, 837, 9, 16049, 16, 10, 1030, 1385, 11, 50264, 6920, 4, 2]
[0, 381, 7823, 28191, 837, 9, 16049, 16, 10, 1030, 1385, 11, 18414, 50264, 4, 2]
PPPL: 655.3166982415099
10804
[0, 381, 7823, 28191, 837, 9, 16049, 16, 10, 1030, 1385, 11, 50264, 1245, 4, 2]
[0, 381, 7823, 28191, 837, 9, 16049, 16, 10, 1030, 1385, 11, 11053, 50264, 4, 2]
PPPL: 34895.063485791
10805
[0, 381, 7823, 28191, 837, 9, 16049, 16, 10, 1030, 1385, 11, 50264, 268, 25134, 4, 2]
[0, 381, 7823, 28191, 837, 9, 16049, 16, 10, 1030, 1385, 11, 3773, 50264, 25134, 4, 2]
[0, 381, 7823, 28191, 837, 9, 16049, 16, 10, 1030, 138

PPPL: 84.00769333231634
10831
[0, 2393, 2832, 39268, 1384, 837, 16, 10, 1030, 1385, 11, 50264, 11489, 282, 1245, 4, 2]
[0, 2393, 2832, 39268, 1384, 837, 16, 10, 1030, 1385, 11, 4058, 50264, 282, 1245, 4, 2]
[0, 2393, 2832, 39268, 1384, 837, 16, 10, 1030, 1385, 11, 4058, 11489, 50264, 1245, 4, 2]
[0, 2393, 2832, 39268, 1384, 837, 16, 10, 1030, 1385, 11, 4058, 11489, 282, 50264, 4, 2]
PPPL: 13.556351512925087
10832
[0, 3303, 3624, 837, 9, 16049, 16, 10, 1030, 1385, 11, 50264, 12, 19897, 3624, 4, 2]
[0, 3303, 3624, 837, 9, 16049, 16, 10, 1030, 1385, 11, 18933, 50264, 19897, 3624, 4, 2]
[0, 3303, 3624, 837, 9, 16049, 16, 10, 1030, 1385, 11, 18933, 12, 50264, 3624, 4, 2]
[0, 3303, 3624, 837, 9, 16049, 16, 10, 1030, 1385, 11, 18933, 12, 19897, 50264, 4, 2]
PPPL: 65.77031159351154
10833
[0, 3303, 3624, 837, 9, 16049, 16, 10, 1030, 1385, 11, 50264, 6920, 4, 2]
[0, 3303, 3624, 837, 9, 16049, 16, 10, 1030, 1385, 11, 12024, 50264, 4, 2]
PPPL: 1262.9081664499001
10834
[0, 3303, 3624, 837, 9, 16049

In [ ]:
mask_inds

In [209]:
tokenized_sentence_with_masks

[0, 2618, 3040, 1974, 13, 50264, 50264, 4, 2]

In [210]:
tokenized_sentence_orig

[0, 2618, 3040, 1974, 13, 5854, 13170, 4, 2]

In [215]:
sum_ppl = 0
n_subtokens_total = num_correct_masks
for mask_j in range(num_correct_masks):
    print(mask_j)
    # find index of current mask (in tokenized seuence)
    index_of_current_mask = mask_inds[mask_j]
    
    # change it with mask id   
    tokenized_sentence = tokenized_sentence_orig.copy()
    tokenized_sentence[index_of_current_mask] = tokenizer.mask_token_id 
    print(tokenized_sentence)
    
    # correct label token id 
    current_correct_token_id = label_ids_i[mask_j]
    
    with torch.no_grad():
        # tensor
        inp = torch.tensor([tokenized_sentence]).cuda() if cuda else torch.tensor([tokenized_sentence])
        
        # get logits
        out = model(inp)
        logits = out.logits.detach().cpu()  # batch_size x max_len x vocab
        
        # logit for the correct token
        logits_for_mask = logits[:,index_of_current_mask][0]
        log_softmax_for_mask = logits_for_mask.log_softmax(-1)
        
        # log_softmax of correct label
        score = log_softmax_for_mask[current_correct_token_id].item()
        print(score)
        sum_ppl += score
pseudo_ppl = math.e**(-1*(sum_ppl/n_subtokens_total))

0
[0, 2618, 3040, 1974, 13, 50264, 13170, 4, 2]
-3.4904656410217285
1
[0, 2618, 3040, 1974, 13, 5854, 50264, 4, 2]
-7.165990352630615


In [213]:
pseudo_ppl

206.07248932667864

In [188]:
logits[:,index_of_current_mask][0].log_softmax(-1)

tensor([-26.1457, -25.0341, -27.8418,  ..., -19.2415, -18.3063, -26.6231])

In [178]:
logits.log_softmax()

TypeError: log_softmax() received an invalid combination of arguments - got (), but expected one of:
 * (int dim, torch.dtype dtype)
 * (name dim, *, torch.dtype dtype)


In [123]:
tokenized_sentence_orig

[0, 2618, 3040, 1974, 13, 50264, 50264, 4, 2]

In [113]:
pred_tokens_without_space = [label[1:] for label in labels_i if label[0]==' ']


In [114]:
pred_tokens_without_space

['Orlando Pride']

In [97]:
list(np.where(np.array(tokenized_sentence_orig) == mask_id)[0])

[5]

In [89]:
text_i

'Alex Morgan plays for <mask>.'

In [75]:
all_res_m0 = fill_mask_model(data_dict_multi_token['2019-Q2']['text'][0])

In [82]:
all_res_m0

[{'score': 0.0853387862443924,
  'token': 4152,
  'token_str': ' Arsenal',
  'sequence': ' Alex Morgan plays for Arsenal.'},
 {'score': 0.061087898910045624,
  'token': 201,
  'token_str': ' us',
  'sequence': ' Alex Morgan plays for us.'},
 {'score': 0.05911916121840477,
  'token': 1156,
  'token_str': ' England',
  'sequence': ' Alex Morgan plays for England.'},
 {'score': 0.045927632600069046,
  'token': 3098,
  'token_str': ' Chelsea',
  'sequence': ' Alex Morgan plays for Chelsea.'},
 {'score': 0.044208161532878876,
  'token': 9692,
  'token_str': ' Everton',
  'sequence': ' Alex Morgan plays for Everton.'},
 {'score': 0.04318976774811745,
  'token': 3426,
  'token_str': ' Liverpool',
  'sequence': ' Alex Morgan plays for Liverpool.'},
 {'score': 0.03067336417734623,
  'token': 8983,
  'token_str': ' Newcastle',
  'sequence': ' Alex Morgan plays for Newcastle.'},
 {'score': 0.024680588394403458,
  'token': 3430,
  'token_str': ' Scotland',
  'sequence': ' Alex Morgan plays for Sco

In [81]:
[correct['score'] for correct in all_res_m0 if correct['token']==data_dict_multi_token['2019-Q2']['labels_ids'][0]]

[]

'Last'

RobertaForMaskedLM(
  (roberta): RobertaModel(
    (embeddings): RobertaEmbeddings(
      (word_embeddings): Embedding(50265, 768, padding_idx=1)
      (position_embeddings): Embedding(514, 768, padding_idx=1)
      (token_type_embeddings): Embedding(1, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): RobertaEncoder(
      (layer): ModuleList(
        (0): RobertaLayer(
          (attention): RobertaAttention(
            (self): RobertaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): RobertaSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNor

In [59]:
fill_mask_model('Flemming Lentfer holds the position of <mask>.')

[{'score': 0.01545275840908289,
  'token': 270,
  'token_str': ' President',
  'sequence': ' Flemming Lentfer holds the position of President.'},
 {'score': 0.011274277232587337,
  'token': 394,
  'token_str': ' president',
  'sequence': ' Flemming Lentfer holds the position of president.'},
 {'score': 0.010287848301231861,
  'token': 3449,
  'token_str': ' captain',
  'sequence': ' Flemming Lentfer holds the position of captain.'},
 {'score': 0.0100465789437294,
  'token': 3957,
  'token_str': ' MP',
  'sequence': ' Flemming Lentfer holds the position of MP.'},
 {'score': 0.0062936292961239815,
  'token': 884,
  'token_str': ' leader',
  'sequence': ' Flemming Lentfer holds the position of leader.'},
 {'score': 0.005673895124346018,
  'token': 155,
  'token_str': ' 3',
  'sequence': ' Flemming Lentfer holds the position of 3.'},
 {'score': 0.005379726178944111,
  'token': 371,
  'token_str': ' third',
  'sequence': ' Flemming Lentfer holds the position of third.'},
 {'score': 0.005079

In [60]:
tokenized_sentence_orig = tokenizer_return_id(tokenizer, text_i)

[{'score': 0.01781419664621353,
  'token': 270,
  'token_str': ' President',
  'sequence': 'Flemming Lentfer holds the position of President.'},
 {'score': 0.01420488953590393,
  'token': 3449,
  'token_str': ' captain',
  'sequence': 'Flemming Lentfer holds the position of captain.'},
 {'score': 0.013646001927554607,
  'token': 394,
  'token_str': ' president',
  'sequence': 'Flemming Lentfer holds the position of president.'},
 {'score': 0.009750999510288239,
  'token': 3957,
  'token_str': ' MP',
  'sequence': 'Flemming Lentfer holds the position of MP.'},
 {'score': 0.006966858170926571,
  'token': 13913,
  'token_str': ' VP',
  'sequence': 'Flemming Lentfer holds the position of VP.'},
 {'score': 0.006721080746501684,
  'token': 884,
  'token_str': ' leader',
  'sequence': 'Flemming Lentfer holds the position of leader.'},
 {'score': 0.00627291202545166,
  'token': 371,
  'token_str': ' third',
  'sequence': 'Flemming Lentfer holds the position of third.'},
 {'score': 0.0058977603

*****

In [83]:
# Load pre-trained model tokenizer (vocabulary)
tokenizer = AutoTokenizer.from_pretrained(lm, use_fast=False, add_prefix_space=True)

CLS = tokenizer.cls_token
PAD = tokenizer.pad_token
SEP = tokenizer.sep_token
MASK = tokenizer.mask_token

mask_id = tokenizer.mask_token_id
sep_id = tokenizer.sep_token_id
cls_id = tokenizer.cls_token_id
pad_id = tokenizer.pad_token_id

special_ids = [mask_id, sep_id, cls_id, pad_id]
def tokenizer_return_id(text, filter_special_tokens=False):
    """
    Text to token ids for a string.
    """
    output = tokenizer(text)
    if filter_special_tokens:
        token_ids = [i for i in output['input_ids'] if i not in tokenizer.all_special_ids]
    else:
        token_ids = [i for i in output['input_ids'] ]
    return token_ids

def tokenize_batch(batch):
    """
    Text to token ids for a list of strings.
    """
#     return [tokenizer.convert_tokens_to_ids(sent) for sent in batch]
    return [tokenizer_return_id(sent) for sent in batch]

def untokenize_id(ids):
    """
    Token ids to strings.
    """
#     return [tokenizer.convert_tokens_to_ids(sent) for sent in batch]
    return [tokenizer.decode(_id) for _id in ids]


def untokenize_batch(batch, filter_special_tokens=False):
    """
    Token ids to strings for a list of ids.
    """
#     return [tokenizer.convert_ids_to_tokens(sent) for sent in batch]
#     print(label_id)
    if filter_special_tokens:
        _batch = []
        for sent in batch:
            _batch.append([x for x in sent if x not in special_ids])
        batch = _batch
#         return [tokenizer.decode(label_id) for label_id in batch if label_id not in special_ids]
#     else:
    return [untokenize_id(sent) for sent in batch]

def detokenize(sent):
    """ Roughly detokenizes (mainly undoes wordpiece) """
    # not sure what this does.... their code
    new_sent = []
    for i, tok in enumerate(sent):
        if tok.startswith("##"):
            new_sent[len(new_sent) - 1] = new_sent[len(new_sent) - 1] + tok[2:]
        else:
            new_sent.append(tok)
    return new_sent

In [594]:
def split_dataset(data):
    """
    Split temporal dataset Dt to D_unchanged, D_new and D_updated compared to D_(t-1) for all t.
    Specifically:
    - D_unchanged: data where text_t = text_(t-1) & label_t = label_(t-1)
    - D_updated: data where text_t = text_(t-1) & label_t != label_(t-1)
    - D_new: data where text_t not in D_(t-1)
    - D_deleted: data that exist in D_(t-1) but not in D_t

    Args:
        data: a dictionary with keys the time (year/quarter/month) and values dictionaries
        data = {
                '2019-Q1':
                    {
                    'text': [list of text],
                    'labels': [list of labels],
                    'labels_ids': [list of label token ids -- for a given model/tokenizer],
                    'relations' [list of Wikidata relations]
                    },
                '2019-Q2': {...}
                }

    Returns:
        D_unchanged, D_new, D_updated, D_deleted
    """
    unchanged_t, new_t, updated_t, deleted_t = {}, {}, {}, {}
    quarters = list(data.keys())
    t_0 = quarters[0]  # t=t0
    t_1 = quarters[0]  # t-1

    for t in quarters[1:]:
        if t in ['2022-Q3', '2022-Q4']:
            continue # skip last two quarters of 2022
        data_t = data[t]      # D_t
        data_t_1 = data[t_1]  # D_(t-1)

        unchanged_t[t] = {key: [] for key in data_t.keys()}
        new_t[t] = {key: [] for key in data_t.keys()}
        updated_t[t] = {key: [] for key in data_t.keys()}
        deleted_t[t] = {key: [] for key in data_t.keys()}

        for i in range(0, len(data_t['text'])): # for all facts in t
            text_t = data_t['text'][i]
            labels_ids_t = data_t['labels_ids'][i][0]
            if text_t in data_t_1['text']:  # if fact in t in facts of t-1
                t_1_index = data_t_1['text'].index(text_t)
                labels_inds_t_1 = data_t_1['labels_ids'][t_1_index][0]
                if labels_ids_t == labels_inds_t_1:
                    # text_t = text_t-1 & label_t = label_t-1
                    # add to D_unchanged
                    for key in data_t.keys():
                        unchanged_t[t][key].append(data_t[key][i])
                else:
                    # text_t = text_(t-1) & label_t != label_(t-1)
                    # add to D_updated
                    for key in data_t.keys():
                        updated_t[t][key].append(data_t[key][i])
            else:
                # text_t not in D_(t-1) texts
                # add to D_new
                for key in data_t.keys():
                    new_t[t][key].append(data_t[key][i])
        for j in range(0, len(data_t_1['text'])):
            text_t_1 = data_t_1['text'][j]
            if text_t_1 not in data_t['text']:
                # text_(t+1) not in D_t
                # add to D_deleted
                for key in data_t_1.keys():
                    deleted_t[t][key].append(data_t_1[key][j])
        t_1 = t

        assert len(data_t['text']) == len(unchanged_t[t]['text']) + len(updated_t[t]['text']) + len(new_t[t]['text'])
        print(
            't={}: From total {} samples in D_t, {} are unchanged, {} are updated, {} are deleted and {} are new, compared to D_(t-1).'.format(
                t,
                len(data_t['text']),
                len(unchanged_t[t]['text']),
                len(updated_t[t]['text']),
                len(deleted_t[t]['text']),
                len(new_t[t]['text'])))
    return unchanged_t, new_t, updated_t, deleted_t, data[t_0]

## Split dataset

In [595]:
# Split dataset
unchanged_t, new_t, updated_t, deleted_t, orig = split_dataset(data_dict_multi_token)

t=2019-Q2: From total 7962 samples in D_t, 7728 are unchanged, 36 are updated, 206 are deleted and 198 are new, compared to D_(t-1).
t=2019-Q3: From total 8011 samples in D_t, 7633 are unchanged, 65 are updated, 264 are deleted and 313 are new, compared to D_(t-1).
t=2019-Q4: From total 7989 samples in D_t, 7742 are unchanged, 51 are updated, 218 are deleted and 196 are new, compared to D_(t-1).
t=2020-Q1: From total 7872 samples in D_t, 7359 are unchanged, 107 are updated, 524 are deleted and 406 are new, compared to D_(t-1).
t=2020-Q2: From total 7848 samples in D_t, 7699 are unchanged, 30 are updated, 143 are deleted and 119 are new, compared to D_(t-1).
t=2020-Q3: From total 7900 samples in D_t, 7666 are unchanged, 40 are updated, 142 are deleted and 194 are new, compared to D_(t-1).
t=2020-Q4: From total 7892 samples in D_t, 7682 are unchanged, 26 are updated, 192 are deleted and 184 are new, compared to D_(t-1).
t=2021-Q1: From total 7819 samples in D_t, 7381 are unchanged, 69 ar

In [600]:
updated_t['2022-Q2']

{'text': [['Nemanja Nikolić plays for <mask> <mask> <mask> <mask> <mask>.'],
  ['Chris Heaton-Harris holds the position of <mask> <mask> <mask> <mask> <mask>.'],
  ['Katy Gallagher holds the position of <mask> <mask> <mask> <mask> <mask>.'],
  ['Antti Kurvinen holds the position of <mask> <mask> <mask> <mask> <mask>.'],
  ['Bridget Brink holds the position of <mask> <mask> <mask> <mask> <mask>.'],
  ['Christian Wakeford is a member of the <mask> <mask>.'],
  ['Gabriëlle Popken is a member of the <mask> <mask> <mask>.'],
  ['<mask> <mask> <mask> <mask> <mask> is the chair of Democratic Party.'],
  ['<mask> <mask> <mask> <mask> <mask> is the chair of Democratic Party.'],
  ['<mask> <mask> <mask> is the head of the government of Pittsburgh.'],
  ['<mask> <mask> is the head of the government of Portland.'],
  ['<mask> <mask> <mask> <mask> is the head coach of Galatasaray S.K..'],
  ['<mask> <mask> <mask> <mask> is the head coach of AC Sparta Prague.'],
  ['<mask> <mask> <mask> <mask> <mask

## Calculate distribution of correct number of masks for each relation in the dataset

In [596]:
num_masks_per_relation = {'relation': [], 'num_masks': []}
rels = []
avg_masks = []
for key,data in data_dict_multi_token.items():
    num_masks_per_relation['relation'] += data['relation']
    num_masks_per_relation['num_masks'] += data['num_masks']

In [597]:
df = pd.DataFrame(data=num_masks_per_relation)
df['avg_num_masks'] = df['num_masks'].apply(lambda l: np.mean(l))

In [598]:
# add histogram
for relation in list(set(df['relation'])):
    rel_avg_masks = df[df['relation']==relation]['avg_num_masks']
    mean = rel_avg_masks.mean()
    std = rel_avg_masks.std()
    print('Relation {} has {}+-{} masks.'.format(relation, mean, std))

Relation P108 has 3.2557063380647846+-1.0566433779824 masks.
Relation P488 has 3.7991272946133012+-1.0440151510212339 masks.
Relation P39 has 2.8759821987344414+-1.2484631699010644 masks.
Relation P102 has 3.0394688306897826+-1.0380073991779586 masks.
Relation P69 has 3.3333333333333335+-0.8677908410058633 masks.
Relation P127 has 3.0933882676083972+-1.0390291009634056 masks.
Relation P6 has 3.7954545454545454+-1.0120816013870382 masks.
Relation P286 has 3.7844364937388195+-1.0331849038301197 masks.
Relation P279 has 3.5+-0.8728715609439694 masks.
Relation P54 has 4.093302066539645+-0.9763579711325114 masks.


## We will filter examples at max M=5 number of masks, as in [Jiang et al., 2020](https://aclanthology.org/2020.emnlp-main.479/)

-----

## Multi-token generation

In [481]:
from transformers import AutoTokenizer, AutoModel, pipeline
lm = "cardiffnlp/twitter-roberta-base-mar2022"
fill_mask_model = pipeline(
    'fill-mask', model=lm, framework="pt",
    tokenizer=tokenizer, top_k=100
)
model = fill_mask_model.model
model.eval()
cuda = torch.cuda.is_available()
if cuda:
    model = model.cuda()
year='2019-Q1'
batch_size = 100
N = batch_size # number of shots
temperature = 1.0
burnin = 200

Downloading: 100%|█████████████████████████████████████████████████████████████| 725/725 [00:00<00:00, 196kB/s]
Downloading: 100%|██████████████████████████████████████████████████████████| 476M/476M [05:34<00:00, 1.49MB/s]


In [485]:
def generate_step(out, gen_idx, temperature=None, top_k=0, sample=False, return_list=True, num_masks=0):
    """ Generate a word from out[gen_idx]

    args:
        - out (torch.Tensor): tensor of logits of size batch_size x seq_len x vocab_size
        - gen_idx (int): location for which to generate for
        - top_k (int): if >0, only sample from the top k most probable words
        - sample (Bool): if True, sample from full distribution. Overridden by top_k
    """
    logits = out[:, gen_idx]
    if num_masks==1:  # if single-token then return the argmax
        idx = torch.argmax(logits, dim=-1)
        return idx.tolist() if return_list else idx
    else:
        if temperature is not None:
            logits = logits / temperature
        if top_k > 0:
            kth_vals, kth_idx = logits.topk(top_k, dim=-1)
            dist = torch.distributions.categorical.Categorical(logits=kth_vals)
            idx = kth_idx.gather(dim=1, index=dist.sample().unsqueeze(-1)).squeeze(-1)
        elif sample:
            dist = torch.distributions.categorical.Categorical(logits=logits)
            idx = dist.sample().squeeze(-1)
        else:
            idx = torch.argmax(logits, dim=-1)
        return idx.tolist() if return_list else idx

In [486]:
text_list = data_dict_multi_token[year]['text']
labels_list = data_dict_multi_token[year]['labels']
labels_ids_list = data_dict_multi_token[year]['labels_ids']
relation_list = data_dict_multi_token[year]['relation']
num_answers_list = data_dict_multi_token[year]['num_answers']

In [487]:
data_dict_multi_token

{'2019-Q1': {'text': [['Alex Morgan plays for <mask> <mask> <mask> <mask> <mask> <mask> <mask>.'],
   ['Lionel Messi plays for <mask> <mask>.'],
   ['Cristiano Ronaldo plays for <mask> <mask> <mask> <mask> <mask>.'],
   ['LeBron James plays for <mask> <mask> <mask>.'],
   ['Puck Moonen plays for <mask> <mask> <mask> <mask> <mask>.'],
   ['Zlatan Ibrahimović plays for <mask> <mask> <mask> <mask> <mask>.'],
   ['Neymar plays for <mask> <mask> <mask> <mask>.'],
   ['Ronaldinho plays for <mask> <mask> <mask> <mask> <mask> <mask>.'],
   ["Samuel Eto'o plays for <mask> <mask>."],
   ['Megan Rapinoe plays for <mask> <mask>.'],
   ['Pau Gasol plays for <mask> <mask> <mask>.'],
   ['Alisha Lehmann plays for <mask> <mask> <mask> <mask> <mask> <mask> <mask>.'],
   ['Robert Lewandowski plays for <mask> <mask> <mask>.'],
   ['Gianluigi Buffon plays for <mask> <mask> <mask> <mask> <mask> <mask> <mask> <mask> <mask> <mask>.'],
   ['Andrea Pirlo plays for <mask> <mask> <mask> <mask>.'],
   ['Kevin Dur

### For a single test example:

In [488]:
i = 0  # for i in range(0, len(text_list)) i is in [0,#test examples]

In [489]:
len(text_list)

11238

In [497]:
text_i = text_list[i]
# text_i = ['The name of the current president of the United States is <mask> <mask>.']
labels_i = labels_list[i][0]
labels_ids_i = labels_ids_list[i][0] # there is an 'extra' list that is why we put [0]
relation_i = relation_list[i]
num_answers_i = num_answers_list[i]
print('Example: {}, Labels: {}, Ids: {}'.format(text_i, labels_i, labels_ids_i))

Example: ['Alex Morgan plays for <mask> <mask> <mask> <mask> <mask> <mask> <mask>.'], Labels: [" United States women's national soccer team"], Ids: [315, 532, 390, 18, 632, 4191, 165]


In [498]:
generated_seq_tokens = [[] for _ in range(batch_size)]  # for each trial
logits_list = [[] for _ in range(batch_size)]

In [499]:
# tokenize text
tokenized_sentence = tokenizer_return_id(text_i)[0]

# mask indices to generate
mask_inds = list(np.where(np.array(tokenized_sentence) == mask_id)[0])

# number of masks (tokens)
M = len(mask_inds)

# create batch (same input, N times)
tokenized_sentence_b = [tokenized_sentence for _ in range(batch_size)]

In [500]:
mask_inds

[5, 6, 7, 8, 9, 10, 11]

In [501]:
for m in mask_inds:
    # tensor
    inp = torch.tensor(tokenized_sentence_b).cuda() if cuda else torch.tensor(tokenized_sentence_b)

    # get logits
    out = model(inp)
    logits = out.logits  # batch_size x max_len x vocab

    # get new ids
    idxs_b = generate_step(logits, gen_idx=m, top_k=10, temperature=temperature, # sample=(m < burnin)
                          )

    # replace mask with predicted token id
    tokenized_sentence_b_np = np.array(tokenized_sentence_b)                       
    tokenized_sentence_b_np[:,m] = np.array(idxs_b)
    tokenized_sentence_b = tokenized_sentence_b_np.tolist() 

    # the following code does not work *and I don't know why*
    # for jj in range(len(idxs_b)):
    #     print('before: {}, predicted token id: {}'.format(tokenized_sentence_b[jj][m],idxs_b[jj]))
    #     tokenized_sentence_b[jj][m] = idxs_b[jj]

    assert sorted(idxs_b) == sorted([sent[m] for sent in tokenized_sentence_b])

    # find logits
    logits_m = logits[:,m]  # logits for the mask in position m
    logits_b = logits_m[:,idxs_b].tolist()[0]  # logits for sampled tokens

    assert len(idxs_b) == len(logits_b)

    # add generated tokens and corresponding logits to lists
    for j in range(N):
        generated_seq_tokens[j].append(idxs_b[j])
        logits_list[j].append(logits_b[j])

In [502]:
# calculate sum of logits for each generated sequence of tokens
sum_logits = np.array(logits_list).sum(axis=-1)

# finding ranking (return indices of the parallel lists for logits and generated tokens)
ranked_inds_of_list = sum_logits.argsort()[::-1]

# ranked logits sum in descending order
ranked_logits = sum_logits[ranked_inds_of_list]

# ranked generated tokens in descending order
ranked_generated_tokens = np.array(generated_seq_tokens)[ranked_inds_of_list]

In [503]:
for no, p in enumerate(ranked_generated_tokens):
    print('{}: {}'.format(no,"".join(untokenize_id(p))))

0:  the @OfficialFAFA right now
1:  the @OfficialBRFC as well
2:  the #AFCAFLs
3:  the U.S. national team
4:  the @CelticFC side
5:  the @LFC and are amazing
6:  the U.K. national team
7:  the #Eagles in this game
8:  the @user @user @user
9:  the @Saints at the moment
10:  the #Rams for the season
11:  the @LFC against #Arsenal
12:  the @Rovers at 10 tonight
13:  the #Eagles at the minute
14:  the @Eagles in a minute
15:  the #Eagles in the game
16:  the @user as the youth manager
17:  the #Bears on the night
18:  the @user on Friday at home
19:  the U.S. Soccer Team
20:  the #Rays in this clip
21:  the @user to start the game
22:  the US national team in this match
23:  the @user today at the Stadium
24:  the @user as his first international
25:  the @Lions tonight in Philly
26:  @RangersFC as the forward
27:  the #LeedsCity side today
28:  the @user in the home opener
29:  @user and @user this weekend
30:  the Red Devils. That's it
31:  @user and @user on Thursday
32:  the #Bills, p

## Evaluation

TempLAMA: "F1 score, which captures the precision 
    and recall that words chosen as being part of the answer are actually part of the answer."

In [504]:
# compare with gold labels
import evaluate
assert len(labels_ids_i) == M
f1_micro_list, f1_macro_list = [], []
rouge_list, bleu_list = [], []

rouge = evaluate.load('rouge')
bleu = evaluate.load("bleu")

In [505]:
labels_ids_i

[315, 532, 390, 18, 632, 4191, 165]

In [507]:
ranked_generated_tokens

array([[    5,   787, 34111,  5944,  5944,   235,   122],
       [    5,   787, 34111,  7202,  5268,    25,   157],
       [    5,   849,   250,  5268,   250,  7613,    29],
       [    5,   121,     4,   104,     4,   632,   165],
       [    5,   787,   347,  6607,   636,  5268,   526],
       [    5,   787,   574,  5268,     8,    32,  2770],
       [    5,   121,     4,   530,     4,   632,   165],
       [    5,   849,   717, 26007,    11,    42,   177],
       [    5,   787, 12105,   787, 12105,   787, 12105],
       [    5,   787,   104, 24487,    23,     5,  1151],
       [    5,   849,   500,  7042,    13,     5,   191],
       [    5,   787,   574,  5268,   136,   849, 31661],
       [    5,   787,   500, 13507,    23,   158,  3422],
       [    5,   849,   717, 26007,    23,     5,  2289],
       [    5,   787,   717, 26007,    11,    10,  2289],
       [    5,   849,   717, 26007,    11,     5,   177],
       [    5,   787, 12105,    25,     5,  2719,  1044],
       [    5,

In [509]:
for j in range(0,N):
    gold_ids = labels_ids_i
    pred_ids_j = ranked_generated_tokens[j]
    gold_tok = labels_i  # list of strings
    pred_tok_j = ["".join(untokenize_id(ranked_generated_tokens[j]))] # list of strings
    
    # F1 score
    # F1_micro calculates metrics globally by counting the total true positives, 
    # false negatives and false positives.
    f1_micro_list.append(f1_score(gold_ids,pred_ids_j, average='micro')) 
    # F1_macro calculates metrics for each label, and finds their unweighted mean. 
    # This does not take label imbalance into account.
    f1_macro_list.append(f1_score(gold_ids,pred_ids_j, average='macro'))
    
    # BLEU
    bleu_list.append(bleu.compute(references=gold_tok,
              predictions=pred_tok_j)['bleu'])

    # ROUGE
    rouge_list.append(rouge.compute(references=gold_tok,
                  predictions=pred_tok_j))
    
    # exact match / P@1
max_f1_micro = np.array(f1_micro_list).max()
max_f1_macro = np.array(f1_macro_list).max()
max_bleu = np.array(bleu_list).max()

In [512]:
f1_macro_list

[0.0,
 0.0,
 0.0,
 0.09090909090909091,
 0.0,
 0.0,
 0.09090909090909091,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.08333333333333333,
 0.0,
 0.08333333333333333,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.07692307692307693,
 0.0,
 0.0,
 0.0,
 0.0,
 0.08333333333333333,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0]

In [234]:
["".join(untokenize_id(ranked_generated_tokens[42]))]

[' luxury cars']

In [235]:
bleu.compute(references=labels_i,
              predictions=["".join(untokenize_id(ranked_generated_tokens[42]))])

{'bleu': 0.0,
 'precisions': [0.0, 0.0, 0.0, 0.0],
 'brevity_penalty': 1.0,
 'length_ratio': 1.0,
 'translation_length': 2,
 'reference_length': 2}

In [236]:
rouge_list

[{'rouge1': AggregateScore(low=Score(precision=0.0, recall=0.0, fmeasure=0.0), mid=Score(precision=0.0, recall=0.0, fmeasure=0.0), high=Score(precision=0.0, recall=0.0, fmeasure=0.0)),
  'rouge2': AggregateScore(low=Score(precision=0.0, recall=0.0, fmeasure=0.0), mid=Score(precision=0.0, recall=0.0, fmeasure=0.0), high=Score(precision=0.0, recall=0.0, fmeasure=0.0)),
  'rougeL': AggregateScore(low=Score(precision=0.0, recall=0.0, fmeasure=0.0), mid=Score(precision=0.0, recall=0.0, fmeasure=0.0), high=Score(precision=0.0, recall=0.0, fmeasure=0.0)),
  'rougeLsum': AggregateScore(low=Score(precision=0.0, recall=0.0, fmeasure=0.0), mid=Score(precision=0.0, recall=0.0, fmeasure=0.0), high=Score(precision=0.0, recall=0.0, fmeasure=0.0))},
 {'rouge1': AggregateScore(low=Score(precision=0.0, recall=0.0, fmeasure=0.0), mid=Score(precision=0.0, recall=0.0, fmeasure=0.0), high=Score(precision=0.0, recall=0.0, fmeasure=0.0)),
  'rouge2': AggregateScore(low=Score(precision=0.0, recall=0.0, fmeasur

In [230]:
np.array(f1_macro_list).max()

0.3333333333333333

In [231]:
np.array(bleu_list).max()

0.0

# All together:

In [299]:
for_logging_dict = {
    'model': None,
    'quarter': None,
    'split': None,
    'logits': None,
    'mlm_scores': None,
    'f1_macro': None,
    'f1_micro': None,
    'bleu': None,
    'rouge':None
    
}
rouge = evaluate.load('rouge')
bleu = evaluate.load("bleu")

max_f1_micro_list, max_f1_macro_list = [], []
max_bleu_list, max_rouge_list = [], []

all_logits_list = []
all_pred_tokens_list = []

for i in tqdm(range(0, 1000)):
    text_i = text_list[i]
    labels_i = labels_list[i][0]
    labels_ids_i = labels_ids_list[i][0] # there is an 'extra' list that is why we put [0]
    relation_i = relation_list[i]
    num_answers_i = num_answers_list[i]
#     print('i={}: Example: {}, Labels: {}, Ids: {}'.format(i, text_i, labels_i, labels_ids_i))
    
    generated_seq_tokens = [[] for _ in range(batch_size)]  # for each trial
    logits_list = [[] for _ in range(batch_size)]

    # tokenize text
    tokenized_sentence = tokenizer_return_id(text_i)[0]

    # mask indices to generate
    mask_inds = list(np.where(np.array(tokenized_sentence) == mask_id)[0])

    # number of masks (tokens)
    M = len(mask_inds)

    # create batch (same input, N times)
    tokenized_sentence_b = [tokenized_sentence for _ in range(batch_size)]

    for m in mask_inds:
        # tensor
        inp = torch.tensor(tokenized_sentence_b).cuda() if cuda else torch.tensor(tokenized_sentence_b)

        # get logits
        out = model(inp)
        logits = out.logits  # batch_size x max_len x vocab

        # get new ids
        idxs_b = generate_step(logits, gen_idx=m, top_k=50, temperature=temperature, # sample=(m < burnin)
                              )

        # replace mask with predicted token id
        tokenized_sentence_b_np = np.array(tokenized_sentence_b)                       
        tokenized_sentence_b_np[:,m] = np.array(idxs_b)
        tokenized_sentence_b = tokenized_sentence_b_np.tolist() 

        # the following code does not work *and I don't know why*
        # for jj in range(len(idxs_b)):
        #     print('before: {}, predicted token id: {}'.format(tokenized_sentence_b[jj][m],idxs_b[jj]))
        #     tokenized_sentence_b[jj][m] = idxs_b[jj]

        assert sorted(idxs_b) == sorted([sent[m] for sent in tokenized_sentence_b])

        # find logits
        logits_m = logits[:,m]  # logits for the mask in position m
        logits_b = logits_m[:,idxs_b].tolist()[0]  # logits for sampled tokens

        assert len(idxs_b) == len(logits_b)

        # add generated tokens and corresponding logits to lists
        for j in range(N):
            generated_seq_tokens[j].append(idxs_b[j])
            logits_list[j].append(logits_b[j])
    
    # calculate sum of logits for each generated sequence of tokens
    sum_logits = np.array(logits_list).sum(axis=-1)

    # finding ranking (return indices of the parallel lists for logits and generated tokens)
    ranked_inds_of_list = sum_logits.argsort()[::-1]

    # ranked logits sum in descending order
    ranked_logits = sum_logits[ranked_inds_of_list]

    # ranked generated tokens in descending order
    ranked_generated_tokens = np.array(generated_seq_tokens)[ranked_inds_of_list]
    
    all_logits_list.append(ranked_logits)
    all_pred_tokens_list.append(ranked_generated_tokens)
    
    # Evaluation
#     print('Evaluation!')
    f1_micro_i, f1_macro_i = [], []
    rouge_i, bleu_i = [], []

    gold_ids = labels_ids_i
    gold_tok = labels_i  # list of strings
    
    for j in range(N):    
        pred_ids_j = ranked_generated_tokens[j]
        pred_tok_j = ["".join(untokenize_id(ranked_generated_tokens[j]))] # list of strings

        # F1 score
        # F1_micro calculates metrics globally by counting the total true positives, 
        # false negatives and false positives.
        f1_micro_i.append(f1_score(gold_ids,pred_ids_j, average='micro')) 
        # F1_macro calculates metrics for each label, and finds their unweighted mean. 
        # This does not take label imbalance into account.
        f1_macro_i.append(f1_score(gold_ids,pred_ids_j, average='macro'))

        # BLEU
#         bleu_i.append(bleu.compute(references=gold_tok,
#                   predictions=pred_tok_j)['bleu'])

#         # ROUGE
#         rouge_i.append(rouge.compute(references=gold_tok,
#                       predictions=pred_tok_j))

        # exact match / P@1
        
    max_f1_micro_list.append(np.array(f1_micro_i).max())
    max_f1_macro_list.append(np.array(f1_macro_i).max())
#     max_bleu_list.append(np.array(bleu_i).max())
    print('Avg f1_micro {}, Avg f1_macro {}'.format(np.mean(max_f1_micro_list), np.mean(max_f1_macro_list)))


  0%|                                                                                                      | 1/1000 [00:03<56:53,  3.42s/it]

Avg f1_micro 0.14285714285714285, Avg f_macro 0.07692307692307693


  0%|▏                                                                                                     | 2/1000 [00:04<29:59,  1.80s/it]

Avg f1_micro 0.07142857142857142, Avg f_macro 0.038461538461538464


  0%|▎                                                                                                     | 3/1000 [00:06<33:08,  1.99s/it]

...

Avg f1_micro 0.12951595832357357, Avg f_macro 0.07611831941255644


100%|█████████████████████████████████████████████████████████████████████████████████████████████████▉| 999/1000 [1:56:56<00:03,  3.81s/it]

Avg f1_micro 0.12952931286264618, Avg f_macro 0.07613312498963004


100%|█████████████████████████████████████████████████████████████████████████████████████████████████| 1000/1000 [1:56:58<00:00,  7.02s/it]

Avg f1_micro 0.12959978354978355, Avg f_macro 0.0761819918646404


In [294]:
np.mean([36, 46, 35, 345])

115.5

In [290]:
["".join(untokenize_id(c)) for c in ranked_generated_tokens]

[' the first time in years',
 ' the first time since 2015',
 ' the first time since 2015',
 ' the best player in history',
 ' his national team in Spain',
 ' the football team of America',
 ' the Brazilian team. Legend',
 " Ronaldo's team in 2020",
 ' the Brazilian team on field',
 ' a different team every game',
 ' the national anthem for Brazil',
 ' the World Cup of Football',
 ' the United States of America',
 ' the United States of America',
 ' the United States of America',
 ' the United States of America',
 ' the United States of America',
 ' the National team or not',
 ' Real Madrid and never scores',
 ' the best of his teams',
 ' the Ronaldo.  Nice',
 ' the club, not himself',
 ' Real Madrid. ��',
 ' the champions league right now',
 ' the Madrid Madrid football team',
 ' the Real Madrid Real Madrid',
 ' @user today in Argentina',
 ' the reds, apparently',
 ' Portugal, and not Argentina',
 ' a team in their league',
 ' this world Cup as well',
 ' the best of his ability',
 ' th

In [238]:
rouge.compute(references=gold_tok,
                      predictions=pred_tok_j)['rouge1']

AggregateScore(low=Score(precision=0.0, recall=0.0, fmeasure=0.0), mid=Score(precision=0.0, recall=0.0, fmeasure=0.0), high=Score(precision=0.0, recall=0.0, fmeasure=0.0))

In [32]:
np.array(f1_macro).max()

0.07692307692307693

In [25]:
untokenize_id(labels_ids_i)

[' United', ' States', ' women', "'s", ' national', ' soccer', ' team']

In [33]:
untokenize_batch(ranked_generated_tokens[0:10])

[[' the', ' St', '.', ' Louis', ' Louis', ' Blues', ' tonight'],
 [' the', ' @', 'All', 'S', ' considered', 'FC', ' today'],
 [' the', ' game', '.', ' ', ' That', "'s", ' all'],
 [' the', ' @', 'D', 'ynam', 'ites', ' FC', ' today'],
 [' the', ' Panthers', '!', ' 1', '-', '0', ' Panther'],
 [' the', ' @', 'Chief', 's', ' in', ' the', ' fourth'],
 [' the', ' Bills', ' in', ' my', ' head', ' right', ' now'],
 [' the', ' @', 'Rap', 'She', 'et', ' right', ' now'],
 [' the', ' Bears', '.', ' Will', ' be', ' tough', ' loss'],
 [' the', ' #', 'Fal', 'cons', ' on', ' both', ' sides']]

In [ ]:
ranked_logits = sum_logits[ranked_inds_of_list]

In [ ]:
ranked_generated_tokens = np.array(generated_seq_tokens)[ranked_inds_of_list]

In [ ]:
ranked_generated_tokens

In [ ]:
# generate token for each mask in parallel
for m in mask_inds:
    # tensor
    inp = torch.tensor(tokenized_sentence_b).cuda() if cuda else torch.tensor(tokenized_sentence_b)  # shape bs x max_len
    
    # get logits
    out = model(inp)
    logits = out.logits
    
    # get new ids
    idxs = generate_step(logits, gen_idx=m, 
                                 top_k=100, temperature=temperature, 
#                                  sample=(m < burnin)
                                )
    predicted_tokens.append(idxs[0])

In [ ]:
# tokenize text
text_ids = tokenizer_return_id(text)
num_tokens=len(text_ids)
if num_tokens >= max_len:
    text_ids_max_len = text_ids[:max_len] # truncate       
else:
    text_ids_max_len = text_ids + (max_len-num_tokens) * [pad_id] # pad       
assert len(text_ids_max_len) == max_len, len(text_ids_max_len)
batch.append(text_ids_max_len)

## Old stuff

In [ ]:
def load_file(filename):
    """
    :param filename:
    :return:
    """
    data = []
    with open(filename, "r") as f:
        for line in f.readlines():
            data.append(json.loads(line))
    return data

In [ ]:
def tokenizer_return_id(text):
    output = tokenizer(text)
    token_ids = [i for i in output['input_ids'] if i not in tokenizer.all_special_ids]
    return token_ids

In [ ]:
test_data = load_file(TEMPLAMA_NEW_DIR)
years = sorted(list(set([d["date"] for d in test_data])))
# split per year
test_data_dict = {k: {"text": [], "labels": [], "labels_ids": [], "relation": []} for k in years}

In [ ]:
d = test_data[0]
year = d["date"]
relation = d['relation']
if type(d['answer']) is not list: d['answer'] = [d['answer']]
labels_string_list = [label['name'] for label in d['answer']]
labels_ids_list = [tokenizer_return_id(string) for string in labels_string_list]
num_masks_list = [len(tokens) for tokens in labels_ids_list]

In [ ]:
all_answers = [a["name"] for a in d["answer"]]
multiple_masks = [" ".join([mask_token for _ in range(num_masks)]) for num_masks in num_masks_list]

In [ ]:
all_masked_answers = [d["query"].replace("_X_", _mask) for _mask in multiple_masks]

In [ ]:
[a["name"] for a in d["answer"]]

In [ ]:
multiple_masks = [" ".join([mask_token for _ in range(num_masks)]) for num_masks in num_masks_list]

In [ ]:
multiple_masks

In [ ]:
def load_dynamic_templama(filename):
    """
    Our dynamically-created TempLAMA version
    :return:
    """
    single_mask = False
    lowercase = False
    
    test_data = load_file(filename)
    years = sorted(list(set([d["date"] for d in test_data])))
    # split per year
    test_data_dict = {k: {"text": [], "labels": [], "labels_ids": [], "relation": []} for k in years}
    for d in tqdm(test_data):
        year = d["date"]
        relation = d['relation']
        if type(d['answer']) is not list: d['answer'] = [d['answer']]
        labels_string_list = [label['name'] for label in d['answer']]  # list of strings with all the labels
        if lowercase:
            labels_string_list = [label['name'].lower() for label in d['answer']]
        labels_ids_list = [tokenizer_return_id(string) for string in labels_string_list]  # list of lists with ids
        num_masks_list = [len(tokens) for tokens in labels_ids_list]
        """
        If we want to consider more correct labels we have to change accepted labels
        """
        # If we evaluate only single-token labels
        if single_mask:
            # check if there is answer with one mask
            if 1 in num_masks_list:
                labels_ids_with_one_mask_index = [i for i,l in enumerate(num_masks_list) if l==1]  # list of ids where answer requires one mask/token
                # accepted_labels = list(np.array(labels_string_list)[labels_ids_with_one_mask_index])
                accepted_labels_ids = np.array(labels_ids_list)[labels_ids_with_one_mask_index].tolist()
                accepted_labels = [[tokenizer.decode(label_id)] for label_id in accepted_labels_ids]
                assert len(accepted_labels)==len(accepted_labels_ids)
                assert len(accepted_labels[0])==len(accepted_labels_ids[0])
                text = d["query"].replace("_X_", mask_token)
                if lowercase:
                    text = d["query"].lower().replace("_x_", mask_token)
                
                test_data_dict[year]["text"].append(text)
                test_data_dict[year]["labels"].append(accepted_labels)
                test_data_dict[year]["labels_ids"].append(accepted_labels_ids)
                test_data_dict[year]["relation"].append(relation)
            else:
                # skip this example
                continue
        else: 
            # accept all labels
#             all_answers = [a["name"] for a in d["answer"]]
            multiple_masks = [" ".join([mask_token for _ in range(num_masks)]) for num_masks in num_masks_list]
            all_masked_queries = [d["query"].replace("_X_", _mask) for _mask in multiple_masks]
            if lowercase:
                all_masked_queries = [d["query"].lower().replace("_x_", _mask) for _mask in multiple_masks]
#                 # todo
#                 all_answers = [seq.lower() for seq in d["answer"]]
#                 # replace "_X_" with correct mask token
#                 if single_mask:
#                     text = d["query"].lower().replace("_x_", mask_token)
#                 else:
#                     num_masks = len(all_answers[0].split())
#                     multiple_masks = " ".join([mask_token for _ in range(num_masks)])
#                     text = d["query"].lower().replace("_x_", multiple_masks)
            else:
                multiple_masks = [" ".join([mask_token for _ in range(num_masks)]) for num_masks in num_masks_list]
                # replace _X_ with as many mask tokens as the correct label
                all_masked_queries = [d["query"].replace("_X_", _mask) for _mask in multiple_masks]

                # Because we have multiple correct labels of possibly different number of tokens, 
                # we now have multiple multiple texts (depending on the number of masks)
                # so we append them all separately at the test set
            
            for i in range(len(all_answers)):
                test_data_dict[year]["text"].append(all_masked_queries[i])
                test_data_dict[year]["labels"].append(labels_string_list[i])
                test_data_dict[year]["labels_ids"].append(labels_ids_list[i])
                test_data_dict[year]["relation"].append(relation)

    return test_data_dict

In [ ]:
load_dynamic_templama(TEMPLAMA_NEW_DIR)

In [ ]:
test_data = load_file(filename)

### Original TempLAMA dataset (downloaded from Google Research github repo)
- 2010-2020
- 9 relations
- 1,000 subjects per relation

In [ ]:
orig_templama = load_file(TEMPLAMA_NEW_DIR)

In [ ]:
orig_templama


Number of examples per year:

In [ ]:
Counter([x['date'] for x in orig_templama])

In [ ]:
print('In total: {} examples for all years, {} unique facts.'.format(len(orig_templama), 
      len(set([x['query'] for x in orig_templama]))))

Number of facts per relation:

In [ ]:
Counter([x['relation'] for x in orig_templama])

### Dynamic TempLAMA dataset (by running their code)
- 2019-2020
- 9 relations
- 5,000 subjects per relation

In [ ]:
reproduced_templama = load_file(TEMPLAMA_NEW_DIR)

Number of examples per quarter:


In [ ]:
Counter([x['date'] for x in reproduced_templama])

In [ ]:
print('In total: {} examples for all years, {} unique facts.'.format(len(reproduced_templama), 
      len(set([x['query'] for x in reproduced_templama]))))

Number of facts per relation:


In [ ]:
Counter([x['relation'] for x in reproduced_templama])

In [ ]:
data = load_dynamic_templama(TEMPLAMA_NEW_DIR)

In [ ]:
data['2019-Q1'].keys()

In [ ]:
for quarter in data:
    quarter_dataset = data[quarter]["text"]
    num_examples = len(quarter_dataset)
    num_relations = Counter(data['2019-Q1']['relation']).items()
    print("Quarter {} - num examples {} - relations {}".format(quarter,num_examples,num_relations))
    

In [ ]:
Counter(data['2019-Q1']['relation']).items()

In [ ]:
data_2019_q1 = data['2019-Q1']
data_2019_q2 = data['2019-Q2']

In [ ]:
next(iter(data)) 


In [ ]:
list(data.keys())

In [ ]:
unchanged_t, new_t, updated_t, deleted_t = {}, {}, {}, {}
quarters = list(data.keys())
t_1 = quarters[0]

for t in quarters[1:]:
    data_t = data[t]      # D_t
    data_t_1 = data[t_1]  # D_(t-1)

    unchanged_t[t] = {key:[] for key in data_t.keys()} 
    new_t[t] = {key:[] for key in data_t.keys()} 
    updated_t[t] = {key:[] for key in data_t.keys()} 
    deleted_t[t] = {key:[] for key in data_t.keys()} 

#     for i in range(0,len(data_t_1['text'])):
#         text_t_1 = data_t_1['text'][j]
#         if text_t_1 not in data_t['text']:
#             # text_(t+1) not in D_t
#             # add to D_deleted
#             for key in ['text', 'relation']:
#                 deleted_t[t][key].append(data_t_1[key])
                
    for i in range (0, len(data_t['text'])):
        text_t = data_t['text'][i]
        labels_ids_t = data_t['labels_ids'][i][0]
        if text_t in data_t_1['text']:
            t_1_index = data_t_1['text'].index(text_t)
            labels_inds_t_1 = data_t_1['labels_ids'][t_1_index][0]
            if labels_ids_t == labels_inds_t_1:
                # text_t = text_t-1 & label_t = label_t-1 
                # add to D_unchanged
                for key in data_t.keys():
                    unchanged_t[t][key].append(data_t[key])
            else:
                # text_t = text_(t-1) & label_t != label_(t-1)
                # add to D_updated
                for key in ['text', 'relation']:
                    updated_t[t][key].append(data_t[key])
        else:
            # text_t not in D_(t-1) texts 
            # add to D_new
            for key in ['text', 'relation']:
                new_t[t][key].append(data_t[key])
    for j in range(0,len(data_t_1['text'])):
        text_t_1 = data_t_1['text'][j]
        if text_t_1 not in data_t['text']:
            # text_(t+1) not in D_t
            # add to D_deleted
            for key in ['text', 'relation']:
                deleted_t[t][key].append(data_t_1[key])
    t_1 = t
    
    assert len(data_t['text']) == len(unchanged_t[t]['text']) + len(updated_t[t]['text']) + len(new_t[t]['text'])
    print('t={}: From total {} samples in D_t, {} are unchanged, {} are updated, {} are deleted and {} are new, compared to D_(t-1).'.format(t,
                                                                                                                             len(data_t['text']),
                                                                                                                    len(unchanged_t[t]['text']),
                                                                                                                   len(updated_t[t]['text']),
                                                                                                                                             len(deleted_t[t]['text']),
                                                                                                                   len(new_t[t]['text'])))

            
            

In [ ]:
len(data[quarters[0]]['relation'])

In [ ]:
len(updated_t['text'])

In [ ]:
len(new_t['text'])

In [ ]:
len(data_2019_q2['text'])

In [ ]:
i=0
text_data_2019_q2['text'][i]

In [ ]:
text_t = data_2019_q2['text'][i]

In [ ]:
labels_ids_t = data_2019_q2['labels_ids'][i][0]

In [ ]:
if text_t in data_2019_q1['text']:
    data_2019_q1['text']

In [ ]:
t_1_index = data_2019_q1['text'].index(text_t)

In [ ]:
labels_t_1 = data_2019_q1['labels_ids'][t_1_index][0]

In [ ]:
labels_t_1 == labels_ids_t

In [ ]:
labels_ids_t

In [ ]:
data_2019_q2.keys()

In [ ]:
unchanged_t = {key:[] for key in data_2019_q2.keys()} 

In [ ]:
unchanged_t